In [1]:
from dataset.build_dataset import build_dataset
import mindspore.dataset as ds
import os
import numpy as np
from mindspore.mindrecord import FileWriter
import json

[WARNING] ME(2140:140307601864512,MainProcess):2021-10-13-20:46:37.573.874 [mindspore/run_check/_check_version.py:181] Cuda ['10.1', '11.1'] version(need by mindspore-gpu) is not found, please confirm that the path of cuda is set to the env LD_LIBRARY_PATH, please refer to the installation guidelines: https://www.mindspore.cn/install
[WARNING] ME(2140:140307601864512,MainProcess):2021-10-13-20:46:37.580.929 [mindspore/run_check/_check_version.py:181] Cuda ['10.1', '11.1'] version(need by mindspore-gpu) is not found, please confirm that the path of cuda is set to the env LD_LIBRARY_PATH, please refer to the installation guidelines: https://www.mindspore.cn/install


In [2]:
FEATURES_FILE = "./data/train_data.npy"

features = np.load(FEATURES_FILE)
list_dict = []
for item in features:
    dict_temp = json.loads(item)
    list_dict.append(dict_temp)

In [3]:
len(list_dict[0]['word_ids'])

180

In [4]:
list_dict[0]['word_ids']

[0,
 598,
 2661,
 222,
 5,
 9880,
 2708,
 2346,
 2082,
 11,
 504,
 4432,
 11,
 226,
 2126,
 10067,
 1470,
 116,
 2,
 2,
 29474,
 28108,
 6,
 5,
 334,
 34,
 10,
 4019,
 2048,
 4,
 497,
 1517,
 5,
 4326,
 6919,
 18,
 1637,
 31346,
 16,
 10,
 9030,
 9577,
 9,
 5,
 9880,
 2708,
 4,
 29261,
 11,
 760,
 9,
 5,
 4326,
 6919,
 8,
 2114,
 24,
 6,
 16,
 10,
 7621,
 9577,
 9,
 4845,
 19,
 3701,
 62,
 33161,
 19,
 5,
 7875,
 22,
 39043,
 1459,
 1614,
 1464,
 13292,
 4977,
 845,
 4130,
 7,
 5,
 4326,
 6919,
 16,
 5,
 26429,
 2426,
 9,
 5,
 25095,
 6924,
 4,
 29261,
 639,
 5,
 32394,
 2426,
 16,
 5,
 7461,
 26187,
 6,
 10,
 19035,
 317,
 9,
 9621,
 8,
 12456,
 4,
 85,
 16,
 10,
 24633,
 9,
 5,
 11491,
 26187,
 23,
 226,
 2126,
 10067,
 6,
 1470,
 147,
 5,
 9880,
 2708,
 2851,
 13735,
 352,
 1382,
 7,
 6130,
 6552,
 625,
 3398,
 208,
 22895,
 853,
 1827,
 11,
 504,
 4432,
 4,
 497,
 5,
 253,
 9,
 5,
 1049,
 1305,
 36,
 463,
 11,
 10,
 2228,
 516,
 14,
 15230,
 149,
 155,
 19638,
 8,
 5,
 2610,
 25336

In [5]:
SQUAD_MINDRECORD_FILE = "./data/train_features.mindrecord"

pad = lambda a,i : a[0:i] if len(a) > i else a + [0] * (i-len(a))
pad1 = lambda a,i : a[0:i] if len(a) > i else a + [1] * (i-len(a))
pad_entity = lambda a,i : a[0:i] if len(a) > i else np.append(a,[-1] * (i-len(a)))

for slist in list_dict:
    slist["entity_attention_mask"] = pad(slist["entity_attention_mask"], 24)
    slist["entity_ids"] = pad(slist["entity_attention_mask"], 24)
    slist["entity_segment_ids"] = pad(slist["entity_segment_ids"], 24)
    
    slist["word_ids"] = pad1(slist["word_ids"], 256)
    slist["word_segment_ids"] = pad(slist["word_segment_ids"], 256)
    slist["word_attention_mask"] = pad(slist["word_attention_mask"], 256)
    # entity padding 1
    entity_size = len(slist["entity_position_ids"])
    slist["entity_position_ids"] = np.array(slist["entity_position_ids"])
    temp = [[-1]*24 for i in range(24)]
    for i in range(24):
        if i < entity_size-1:
            temp[i]=(pad_entity(slist["entity_position_ids"][i], 24))


    slist["entity_position_ids"] =temp
    # entity_padding 2
    #slist["entity_position_ids"] = np.array(slist["entity_position_ids"]).flatten()
    #slist["entity_position_ids"] = pad_entity(slist["entity_position_ids"], 24)


if os.path.exists(SQUAD_MINDRECORD_FILE):
    os.remove(SQUAD_MINDRECORD_FILE)
    os.remove(SQUAD_MINDRECORD_FILE + ".db")

writer = FileWriter(file_name=SQUAD_MINDRECORD_FILE, shard_num=1)

data_schema = {
    #"unique_id": {"type": "int32", "shape": [-1]},
    "word_ids": {"type": "int32", "shape": [-1]},
    "word_segment_ids": {"type": "int32", "shape": [-1]},
    "word_attention_mask": {"type": "int32", "shape": [-1]},
    "entity_ids": {"type": "int32", "shape": [-1]},
    "entity_position_ids": {"type": "int32", "shape": [24,24]}, # 
    "entity_segment_ids": {"type": "int32", "shape": [-1]},
    "entity_attention_mask": {"type": "int32", "shape": [-1]},
    "start_positions": {"type": "int32", "shape": [-1]},
    "end_positions": {"type": "int32", "shape": [-1]}
}
writer.add_schema(data_schema, "it is a preprocessed squad dataset")

data = []
i = 0
for item in list_dict:
    i += 1
    sample = {
        #"unique_id": np.array(item["unique_id"], dtype=np.int32),
        "word_ids": np.array(item["word_ids"], dtype=np.int32),
        "word_segment_ids": np.array(item["word_segment_ids"], dtype=np.int32),
        "word_attention_mask": np.array(item["word_attention_mask"], dtype=np.int32),
        "entity_ids": np.array(item["entity_ids"], dtype=np.int32),
        "entity_position_ids": np.array(item["entity_position_ids"], dtype=np.int32),
        "entity_segment_ids": np.array(item["entity_segment_ids"], dtype=np.int32),
        "entity_attention_mask": np.array(item["entity_attention_mask"], dtype=np.int32),
        "start_positions": np.array(item["start_positions"], dtype=np.int32),
        "end_positions": np.array(item["end_positions"], dtype=np.int32),
    }

    data.append(sample)
    #print(sample)
    if i % 10 == 0:
        writer.write_raw_data(data)
        data = []
print(data[0])
if data:
    writer.write_raw_data(data)

writer.commit()

{'word_ids': array([    0,  1740,    99,   343,   473,  1586,  1071, 19252,   904,
         786,  8287,  4871,     7, 15359, 14785,   257,   116,     2,
           2,    20,  1049,   758,  3062,  2754, 15359, 14785,   257,
           8,  4634, 15377,    16,     5, 24311,  6455,  9965,  1016,
        4414,     6,  2034,    59,   411,  8130,    36,   401,  6301,
          36,   246,     4,   406, 11163, 35122,    31,     5,   343,
        2100,     4, 23701,  1070,    30,     5,  5280, 10333,  4305,
           9, 15377,    24,    34,    80, 20531,     6,    65,  1897,
           8,    65,   758,     4,   497,  1455,     6,    59,   820,
         758,  8537,  4686, 15377,     7,    97, 11633,    11,  1005,
           6,  1817,     8,     5,  2367,   953,     6,     7,  1947,
         215,    25, 12275,     6,  3534,     6,   229, 14024,  2186,
           6,  2920,     6, 15398,     6, 18959, 19193,     6,  8086,
        5870,     6, 12600,     6,  2884,   139,     6,   226,  7333,
       

MSRStatus.SUCCESS

In [6]:
columns_list = ['word_ids',  'word_segment_ids', 'word_attention_mask',
               'entity_ids', 'entity_position_ids', 'entity_segment_ids',
               'entity_attention_mask', 'start_positions', 'end_positions']
output_features = np.array(list_dict)
#SQUAD_MINDRECORD_FILE = "./data/dev_features.mindrecord"
data_set = ds.MindDataset(dataset_file=SQUAD_MINDRECORD_FILE, columns_list=columns_list)
count = 0
for item in data_set.create_dict_iterator():
    #print(item)
    count += 1
print("Got {} samples".format(count))

Got 87777 samples


In [7]:
data_set = data_set.batch(2)# , drop_remainder=True
data_sample = next(data_set.create_dict_iterator())
data_sample

{'word_ids': Tensor(shape=[2, 256], dtype=Int32, value=
 [[   0, 4820,   16 ...    1,    1,    1],
  [   0,  287,   10 ...    5, 2949,    8]]),
 'word_segment_ids': Tensor(shape=[2, 256], dtype=Int32, value=
 [[0, 0, 0 ... 0, 0, 0],
  [0, 0, 0 ... 0, 0, 0]]),
 'word_attention_mask': Tensor(shape=[2, 256], dtype=Int32, value=
 [[1, 1, 1 ... 0, 0, 0],
  [1, 1, 1 ... 1, 1, 1]]),
 'entity_ids': Tensor(shape=[2, 24], dtype=Int32, value=
 [[0, 0, 0 ... 0, 0, 0],
  [1, 1, 1 ... 0, 0, 0]]),
 'entity_position_ids': Tensor(shape=[2, 24, 24], dtype=Int32, value=
 [[[ -1,  -1,  -1 ...  -1,  -1,  -1],
   [ -1,  -1,  -1 ...  -1,  -1,  -1],
   [ -1,  -1,  -1 ...  -1,  -1,  -1],
   ...
   [ -1,  -1,  -1 ...  -1,  -1,  -1],
   [ -1,  -1,  -1 ...  -1,  -1,  -1],
   [ -1,  -1,  -1 ...  -1,  -1,  -1]],
  [[ 40,  41,  42 ...  -1,  -1,  -1],
   [142, 143, 144 ...  -1,  -1,  -1],
   [259, 260,  -1 ...  -1,  -1,  -1],
   ...
   [ -1,  -1,  -1 ...  -1,  -1,  -1],
   [ -1,  -1,  -1 ...  -1,  -1,  -1],
   [ -1, 

In [8]:
data_sample['entity_position_ids']

Tensor(shape=[2, 24, 24], dtype=Int32, value=
[[[ -1,  -1,  -1 ...  -1,  -1,  -1],
  [ -1,  -1,  -1 ...  -1,  -1,  -1],
  [ -1,  -1,  -1 ...  -1,  -1,  -1],
  ...
  [ -1,  -1,  -1 ...  -1,  -1,  -1],
  [ -1,  -1,  -1 ...  -1,  -1,  -1],
  [ -1,  -1,  -1 ...  -1,  -1,  -1]],
 [[ 40,  41,  42 ...  -1,  -1,  -1],
  [142, 143, 144 ...  -1,  -1,  -1],
  [259, 260,  -1 ...  -1,  -1,  -1],
  ...
  [ -1,  -1,  -1 ...  -1,  -1,  -1],
  [ -1,  -1,  -1 ...  -1,  -1,  -1],
  [ -1,  -1,  -1 ...  -1,  -1,  -1]]])

In [9]:
data_sample['entity_attention_mask']

Tensor(shape=[2, 24], dtype=Int32, value=
[[0, 0, 0 ... 0, 0, 0],
 [1, 1, 1 ... 0, 0, 0]])

## Train

In [10]:
from readingcomprehension.models.luke import LukeForReadingComprehension, LukeForReadingComprehensionWithLoss, LukeEntityAwareAttentionModel, LukeSquadCell
import mindspore.common.dtype as mstype
from model.bert_model import BertConfig
from mindspore import context, save_checkpoint
from model.luke import LukeModel, EntityAwareEncoder
from mindspore import Tensor, context
from mindspore import dtype as mstype
import mindspore.ops as ops
import mindspore.nn as nn
from model.bert_model import BertOutput
from mindspore.common.initializer import TruncatedNormal
from mindspore.ops import composite as C
import mindspore
from mindspore.ops import operations as P
from mindspore.train.model import Model
from tqdm import tqdm
from mindspore.train.serialization import load_checkpoint, load_param_into_net
from mindspore.train.model import Model
import collections
# PYNATIVE_MODE & GRAPH_MODE
context.set_context(mode=context.GRAPH_MODE, device_target="GPU")
context.set_context(enable_graph_kernel=True)

In [11]:

# def do_train(dataset=None, network=None, load_checkpoint_path="", save_checkpoint_path="", epoch_num=1):
#     """ do train """
#     if load_checkpoint_path == "":
#         raise ValueError("Pretrain model missed, finetune task must load pretrain model!")
#     steps_per_epoch = dataset.get_dataset_size()
#     # optimizer
#     if optimizer_cfg.optimizer == 'AdamWeightDecay':
#         lr_schedule = BertLearningRate(learning_rate=15e-6,
#                                        end_learning_rate=optimizer_cfg.AdamWeightDecay.end_learning_rate,
#                                        warmup_steps=int(steps_per_epoch * epoch_num * 0.1),
#                                        decay_steps=steps_per_epoch * epoch_num,
#                                        power=optimizer_cfg.AdamWeightDecay.power)
#         params = network.trainable_params()
#         decay_params = list(filter(optimizer_cfg.AdamWeightDecay.decay_filter, params))
#         other_params = list(filter(lambda x: not optimizer_cfg.AdamWeightDecay.decay_filter(x), params))
#         group_params = [{'params': decay_params, 'weight_decay': optimizer_cfg.AdamWeightDecay.weight_decay},
#                         {'params': other_params, 'weight_decay': 0.0}]

#         optimizer = AdamWeightDecay(group_params, lr_schedule, eps=optimizer_cfg.AdamWeightDecay.eps)
#     elif optimizer_cfg.optimizer == 'Lamb':
#         lr_schedule = BertLearningRate(learning_rate=optimizer_cfg.Lamb.learning_rate,
#                                        end_learning_rate=optimizer_cfg.Lamb.end_learning_rate,
#                                        warmup_steps=int(steps_per_epoch * epoch_num * 0.1),
#                                        decay_steps=steps_per_epoch * epoch_num,
#                                        power=optimizer_cfg.Lamb.power)
#         optimizer = Lamb(network.trainable_params(), learning_rate=lr_schedule)
#     elif optimizer_cfg.optimizer == 'Momentum':
#         optimizer = Momentum(network.trainable_params(), learning_rate=optimizer_cfg.Momentum.learning_rate,
#                              momentum=optimizer_cfg.Momentum.momentum)
#     else:
#         raise Exception("Optimizer not supported. support: [AdamWeightDecay, Lamb, Momentum]")

#     # load checkpoint into network
#     ckpt_config = CheckpointConfig(save_checkpoint_steps=steps_per_epoch, keep_checkpoint_max=1)
#     ckpoint_cb = ModelCheckpoint(prefix="squad",
#                                  directory=None if save_checkpoint_path == "" else save_checkpoint_path,
#                                  config=ckpt_config)
#     param_dict = load_checkpoint(load_checkpoint_path)
#     load_param_into_net(network, param_dict)

#     update_cell = DynamicLossScaleUpdateCell(loss_scale_value=2 ** 32, scale_factor=2, scale_window=1000)
#     netwithgrads = BertSquadCell(network, optimizer=optimizer, scale_update_cell=update_cell)
#     model = Model(netwithgrads)
#     callbacks = [TimeMonitor(dataset.get_dataset_size()), LossCallBack(dataset.get_dataset_size()), ckpoint_cb]
#     model.train(epoch_num, dataset, callbacks=callbacks)

In [12]:
from mindspore.train.callback import Callback
from mindspore.train.serialization import load_checkpoint, load_param_into_net
from mindspore.train.model import Model
from mindspore.nn.learning_rate_schedule import LearningRateSchedule, PolynomialDecayLR, WarmUpLR
from mindspore.nn.wrap.loss_scale import DynamicLossScaleUpdateCell

import collections
import time
class BertLearningRate(LearningRateSchedule):
    """
    Warmup-decay learning rate for Bert network.
    """

    def __init__(self, learning_rate, end_learning_rate, warmup_steps, decay_steps, power):
        super(BertLearningRate, self).__init__()
        self.warmup_flag = False
        if warmup_steps > 0:
            self.warmup_flag = True
            self.warmup_lr = WarmUpLR(learning_rate, warmup_steps)
        self.decay_lr = PolynomialDecayLR(learning_rate, end_learning_rate, decay_steps, power)
        self.warmup_steps = Tensor(np.array([warmup_steps]).astype(np.float32))

        self.greater = mindspore.ops.Greater()
        self.one = Tensor(np.array([1.0]).astype(np.float32))
        self.cast = mindspore.ops.Cast()

    def construct(self, global_step):
        decay_lr = self.decay_lr(global_step)
        if self.warmup_flag:
            is_warmup = self.cast(self.greater(self.warmup_steps, global_step), mstype.float32)
            warmup_lr = self.warmup_lr(global_step)
            lr = (self.one - is_warmup) * decay_lr + is_warmup * warmup_lr
        else:
            lr = decay_lr
        return lr


class LossCallBack(Callback):
    """
    Monitor the loss in training.

    If the loss is NAN or INF terminating training.

    Note:
        If per_print_times is 0 do not print loss.

    Args:
        per_print_times (int): Print loss every times. Default: 1.
    """

    def __init__(self, per_print_times=1, rank_ids=0):
        super(LossCallBack, self).__init__()
        if not isinstance(per_print_times, int) or per_print_times < 0:
            raise ValueError("print_step must be int and >= 0.")
        self._per_print_times = per_print_times
        self.rank_id = rank_ids
        self.time_stamp_first = get_ms_timestamp()

    def step_end(self, run_context):
        """Monitor the loss in training."""
        time_stamp_current = get_ms_timestamp()
        cb_params = run_context.original_args()
        print("time: {}, epoch: {}, step: {}, outputs are {}".format(time_stamp_current - self.time_stamp_first,
                                                                     cb_params.cur_epoch_num,
                                                                     cb_params.cur_step_num,
                                                                     str(cb_params.net_outputs)))
        with open("./loss_{}.log".format(self.rank_id), "a+") as f:
            f.write("time: {}, epoch: {}, step: {}, loss: {}".format(
                time_stamp_current - self.time_stamp_first,
                cb_params.cur_epoch_num,
                cb_params.cur_step_num,
                str(cb_params.net_outputs[0].asnumpy())))
            f.write('\n')


def get_ms_timestamp():
    t = time.time()
    return int(round(t * 1000))

In [13]:
for i in data_set:
    print(len(i))
    print(i)
    break

9
[Tensor(shape=[2, 256], dtype=Int32, value=
[[   0,  590, 6084 ...    1,    1,    1],
 [   0,  653,  488 ...    1,    1,    1]]), Tensor(shape=[2, 256], dtype=Int32, value=
[[0, 0, 0 ... 0, 0, 0],
 [0, 0, 0 ... 0, 0, 0]]), Tensor(shape=[2, 256], dtype=Int32, value=
[[1, 1, 1 ... 0, 0, 0],
 [1, 1, 1 ... 0, 0, 0]]), Tensor(shape=[2, 24], dtype=Int32, value=
[[1, 1, 1 ... 0, 0, 0],
 [1, 1, 0 ... 0, 0, 0]]), Tensor(shape=[2, 24, 24], dtype=Int32, value=
[[[16, 17, -1 ... -1, -1, -1],
  [39, 40, 41 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  ...
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1]],
 [[50, 51, 52 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  ...
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1],
  [-1, -1, -1 ... -1, -1, -1]]]), Tensor(shape=[2, 24], dtype=Int32, value=
[[0, 0, 0 ... 0, 0, 0],
 [0, 0, 0 ... 0, 0, 0]]), Tensor(shape=[2, 24], dtype=Int32, value=
[[1, 1, 1 ... 0, 0, 0]

In [14]:
epoch=1

luke_config = BertConfig()
LUKEModel = LukeForReadingComprehension(luke_config)
param_dict = load_checkpoint('./luke-large-qa.ckpt')
load_param_into_net(LUKEModel,param_dict)

# update_cell = DynamicLossScaleUpdateCell(loss_scale_value=2 ** 32, scale_factor=2, scale_window=1000)

lukesquad = LukeForReadingComprehensionWithLoss(LUKEModel)

# lr_schedule = BertLearningRate(learning_rate=15e-6,
#                                    end_learning_rate=15e-6 * 0,
#                                    warmup_steps=int(data_set.get_dataset_size() * epoch * 0.1),
#                                    decay_steps=data_set.get_dataset_size() * epoch,
#                                    power=1.0)

update_cell = DynamicLossScaleUpdateCell(loss_scale_value=2 ** 32, scale_factor=2, scale_window=1000)


params = lukesquad.trainable_params()

optimizer = mindspore.nn.AdamWeightDecay(params,
                                         learning_rate=5e-5, #15e-6
                                         beta1=0.9,
                                         beta2=0.98,
                                         eps=1e-06)

# optimizer = mindspore.nn.Adam(params, learning_rate=lr_schedule, eps=1e-8)

# lr_schedule
# warmup_steps=877
num_train_steps=14629
warmup_steps = int(epoch * num_train_steps * 0.06)
netwithgrads = LukeSquadCell(lukesquad,optimizer=optimizer, scale_update_cell=update_cell)
model = Model(netwithgrads)

loss_monitor = LossCallBack()
model.train(epoch,data_set,callbacks=[loss_monitor],dataset_sink_mode=False)




time: 69947, epoch: 1, step: 1, outputs are (Tensor(shape=[], dtype=Float32, value= 6.94353), Tensor(shape=[], dtype=Bool, value= False))
time: 70158, epoch: 1, step: 2, outputs are (Tensor(shape=[], dtype=Float32, value= 5.283), Tensor(shape=[], dtype=Bool, value= False))
time: 70354, epoch: 1, step: 3, outputs are (Tensor(shape=[], dtype=Float32, value= 6.36746), Tensor(shape=[], dtype=Bool, value= False))
time: 70553, epoch: 1, step: 4, outputs are (Tensor(shape=[], dtype=Float32, value= 6.50989), Tensor(shape=[], dtype=Bool, value= False))
time: 70749, epoch: 1, step: 5, outputs are (Tensor(shape=[], dtype=Float32, value= 5.43472), Tensor(shape=[], dtype=Bool, value= False))
time: 70949, epoch: 1, step: 6, outputs are (Tensor(shape=[], dtype=Float32, value= 5.25002), Tensor(shape=[], dtype=Bool, value= False))
time: 71144, epoch: 1, step: 7, outputs are (Tensor(shape=[], dtype=Float32, value= 5.98844), Tensor(shape=[], dtype=Bool, value= False))
time: 71343, epoch: 1, step: 8, outp

time: 82079, epoch: 1, step: 61, outputs are (Tensor(shape=[], dtype=Float32, value= 5.59389), Tensor(shape=[], dtype=Bool, value= False))
time: 82275, epoch: 1, step: 62, outputs are (Tensor(shape=[], dtype=Float32, value= 5.52772), Tensor(shape=[], dtype=Bool, value= False))
time: 82485, epoch: 1, step: 63, outputs are (Tensor(shape=[], dtype=Float32, value= 5.3696), Tensor(shape=[], dtype=Bool, value= False))
time: 82692, epoch: 1, step: 64, outputs are (Tensor(shape=[], dtype=Float32, value= 5.6555), Tensor(shape=[], dtype=Bool, value= False))
time: 82908, epoch: 1, step: 65, outputs are (Tensor(shape=[], dtype=Float32, value= 5.632), Tensor(shape=[], dtype=Bool, value= False))
time: 83119, epoch: 1, step: 66, outputs are (Tensor(shape=[], dtype=Float32, value= 5.54367), Tensor(shape=[], dtype=Bool, value= False))
time: 83322, epoch: 1, step: 67, outputs are (Tensor(shape=[], dtype=Float32, value= 5.64191), Tensor(shape=[], dtype=Bool, value= False))
time: 83520, epoch: 1, step: 68

time: 94329, epoch: 1, step: 121, outputs are (Tensor(shape=[], dtype=Float32, value= 5.48472), Tensor(shape=[], dtype=Bool, value= False))
time: 94528, epoch: 1, step: 122, outputs are (Tensor(shape=[], dtype=Float32, value= 5.47641), Tensor(shape=[], dtype=Bool, value= False))
time: 94728, epoch: 1, step: 123, outputs are (Tensor(shape=[], dtype=Float32, value= 5.59831), Tensor(shape=[], dtype=Bool, value= False))
time: 94926, epoch: 1, step: 124, outputs are (Tensor(shape=[], dtype=Float32, value= 5.48615), Tensor(shape=[], dtype=Bool, value= False))
time: 95124, epoch: 1, step: 125, outputs are (Tensor(shape=[], dtype=Float32, value= 5.52817), Tensor(shape=[], dtype=Bool, value= False))
time: 95321, epoch: 1, step: 126, outputs are (Tensor(shape=[], dtype=Float32, value= 5.51648), Tensor(shape=[], dtype=Bool, value= False))
time: 95549, epoch: 1, step: 127, outputs are (Tensor(shape=[], dtype=Float32, value= 5.77724), Tensor(shape=[], dtype=Bool, value= False))
time: 95755, epoch: 

time: 106530, epoch: 1, step: 181, outputs are (Tensor(shape=[], dtype=Float32, value= 5.61178), Tensor(shape=[], dtype=Bool, value= False))
time: 106728, epoch: 1, step: 182, outputs are (Tensor(shape=[], dtype=Float32, value= 5.66822), Tensor(shape=[], dtype=Bool, value= False))
time: 106927, epoch: 1, step: 183, outputs are (Tensor(shape=[], dtype=Float32, value= 5.63078), Tensor(shape=[], dtype=Bool, value= False))
time: 107126, epoch: 1, step: 184, outputs are (Tensor(shape=[], dtype=Float32, value= 6.42817), Tensor(shape=[], dtype=Bool, value= False))
time: 107327, epoch: 1, step: 185, outputs are (Tensor(shape=[], dtype=Float32, value= 5.6604), Tensor(shape=[], dtype=Bool, value= False))
time: 107524, epoch: 1, step: 186, outputs are (Tensor(shape=[], dtype=Float32, value= 5.39488), Tensor(shape=[], dtype=Bool, value= False))
time: 107724, epoch: 1, step: 187, outputs are (Tensor(shape=[], dtype=Float32, value= 5.63358), Tensor(shape=[], dtype=Bool, value= False))
time: 107921, 

time: 118477, epoch: 1, step: 241, outputs are (Tensor(shape=[], dtype=Float32, value= 5.46832), Tensor(shape=[], dtype=Bool, value= False))
time: 118676, epoch: 1, step: 242, outputs are (Tensor(shape=[], dtype=Float32, value= 5.57896), Tensor(shape=[], dtype=Bool, value= False))
time: 118877, epoch: 1, step: 243, outputs are (Tensor(shape=[], dtype=Float32, value= 5.39134), Tensor(shape=[], dtype=Bool, value= False))
time: 119075, epoch: 1, step: 244, outputs are (Tensor(shape=[], dtype=Float32, value= 5.71646), Tensor(shape=[], dtype=Bool, value= False))
time: 119275, epoch: 1, step: 245, outputs are (Tensor(shape=[], dtype=Float32, value= 5.40743), Tensor(shape=[], dtype=Bool, value= False))
time: 119474, epoch: 1, step: 246, outputs are (Tensor(shape=[], dtype=Float32, value= 5.68486), Tensor(shape=[], dtype=Bool, value= False))
time: 119674, epoch: 1, step: 247, outputs are (Tensor(shape=[], dtype=Float32, value= 5.6308), Tensor(shape=[], dtype=Bool, value= False))
time: 119872, 

...

time: 8848958, epoch: 1, step: 43648, outputs are (Tensor(shape=[], dtype=Float32, value= 5.5198), Tensor(shape=[], dtype=Bool, value= False))
time: 8849166, epoch: 1, step: 43649, outputs are (Tensor(shape=[], dtype=Float32, value= 5.57494), Tensor(shape=[], dtype=Bool, value= False))
time: 8849375, epoch: 1, step: 43650, outputs are (Tensor(shape=[], dtype=Float32, value= 5.54088), Tensor(shape=[], dtype=Bool, value= False))
time: 8849584, epoch: 1, step: 43651, outputs are (Tensor(shape=[], dtype=Float32, value= 5.87687), Tensor(shape=[], dtype=Bool, value= False))
time: 8849784, epoch: 1, step: 43652, outputs are (Tensor(shape=[], dtype=Float32, value= 5.90001), Tensor(shape=[], dtype=Bool, value= False))
time: 8849987, epoch: 1, step: 43653, outputs are (Tensor(shape=[], dtype=Float32, value= 5.72369), Tensor(shape=[], dtype=Bool, value= False))
time: 8850188, epoch: 1, step: 43654, outputs are (Tensor(shape=[], dtype=Float32, value= 5.55713), Tensor(shape=[], dtype=Bool, value= F

time: 8860503, epoch: 1, step: 43705, outputs are (Tensor(shape=[], dtype=Float32, value= 5.4853), Tensor(shape=[], dtype=Bool, value= False))
time: 8860702, epoch: 1, step: 43706, outputs are (Tensor(shape=[], dtype=Float32, value= 5.44503), Tensor(shape=[], dtype=Bool, value= False))
time: 8860900, epoch: 1, step: 43707, outputs are (Tensor(shape=[], dtype=Float32, value= 5.38645), Tensor(shape=[], dtype=Bool, value= False))
time: 8861096, epoch: 1, step: 43708, outputs are (Tensor(shape=[], dtype=Float32, value= 5.67099), Tensor(shape=[], dtype=Bool, value= False))
time: 8861294, epoch: 1, step: 43709, outputs are (Tensor(shape=[], dtype=Float32, value= 5.66972), Tensor(shape=[], dtype=Bool, value= False))
time: 8861490, epoch: 1, step: 43710, outputs are (Tensor(shape=[], dtype=Float32, value= 5.40198), Tensor(shape=[], dtype=Bool, value= False))
time: 8861688, epoch: 1, step: 43711, outputs are (Tensor(shape=[], dtype=Float32, value= 5.62004), Tensor(shape=[], dtype=Bool, value= F

time: 8871770, epoch: 1, step: 43762, outputs are (Tensor(shape=[], dtype=Float32, value= 6.01043), Tensor(shape=[], dtype=Bool, value= False))
time: 8871992, epoch: 1, step: 43763, outputs are (Tensor(shape=[], dtype=Float32, value= 6.20379), Tensor(shape=[], dtype=Bool, value= False))
time: 8872214, epoch: 1, step: 43764, outputs are (Tensor(shape=[], dtype=Float32, value= 5.60054), Tensor(shape=[], dtype=Bool, value= False))
time: 8872438, epoch: 1, step: 43765, outputs are (Tensor(shape=[], dtype=Float32, value= 5.73386), Tensor(shape=[], dtype=Bool, value= False))
time: 8872653, epoch: 1, step: 43766, outputs are (Tensor(shape=[], dtype=Float32, value= 5.6191), Tensor(shape=[], dtype=Bool, value= False))
time: 8872861, epoch: 1, step: 43767, outputs are (Tensor(shape=[], dtype=Float32, value= 5.64045), Tensor(shape=[], dtype=Bool, value= False))
time: 8873069, epoch: 1, step: 43768, outputs are (Tensor(shape=[], dtype=Float32, value= 5.29976), Tensor(shape=[], dtype=Bool, value= F

time: 8883385, epoch: 1, step: 43819, outputs are (Tensor(shape=[], dtype=Float32, value= 5.47249), Tensor(shape=[], dtype=Bool, value= False))
time: 8883586, epoch: 1, step: 43820, outputs are (Tensor(shape=[], dtype=Float32, value= 5.69568), Tensor(shape=[], dtype=Bool, value= False))
time: 8883788, epoch: 1, step: 43821, outputs are (Tensor(shape=[], dtype=Float32, value= 5.47416), Tensor(shape=[], dtype=Bool, value= False))
time: 8883991, epoch: 1, step: 43822, outputs are (Tensor(shape=[], dtype=Float32, value= 5.71465), Tensor(shape=[], dtype=Bool, value= False))
time: 8884193, epoch: 1, step: 43823, outputs are (Tensor(shape=[], dtype=Float32, value= 5.55189), Tensor(shape=[], dtype=Bool, value= False))
time: 8884395, epoch: 1, step: 43824, outputs are (Tensor(shape=[], dtype=Float32, value= 5.68324), Tensor(shape=[], dtype=Bool, value= False))
time: 8884595, epoch: 1, step: 43825, outputs are (Tensor(shape=[], dtype=Float32, value= 5.64861), Tensor(shape=[], dtype=Bool, value= 

time: 8894821, epoch: 1, step: 43876, outputs are (Tensor(shape=[], dtype=Float32, value= 5.40414), Tensor(shape=[], dtype=Bool, value= False))
time: 8895018, epoch: 1, step: 43877, outputs are (Tensor(shape=[], dtype=Float32, value= 5.60201), Tensor(shape=[], dtype=Bool, value= False))
time: 8895215, epoch: 1, step: 43878, outputs are (Tensor(shape=[], dtype=Float32, value= 5.43703), Tensor(shape=[], dtype=Bool, value= False))
time: 8895411, epoch: 1, step: 43879, outputs are (Tensor(shape=[], dtype=Float32, value= 5.81739), Tensor(shape=[], dtype=Bool, value= False))
time: 8895608, epoch: 1, step: 43880, outputs are (Tensor(shape=[], dtype=Float32, value= 5.46911), Tensor(shape=[], dtype=Bool, value= False))
time: 8895806, epoch: 1, step: 43881, outputs are (Tensor(shape=[], dtype=Float32, value= 5.34448), Tensor(shape=[], dtype=Bool, value= False))
time: 8896003, epoch: 1, step: 43882, outputs are (Tensor(shape=[], dtype=Float32, value= 5.54566), Tensor(shape=[], dtype=Bool, value= 

In [15]:

save_checkpoint(model.train_network, ckpt_path / Path("ft.ckpt"))

NameError: name 'save_checkpoint' is not defined